In [1]:
# %matplotlib inline
# import mpld3
# mpld3.enable_notebook()
import rosbag_pandas
import pandas as pd
import matplotlib.pyplot as plt
import easygui
import rosbag
import json
import numpy as np
import cPickle as pkl
import time
def TicTocGenerator():
    # Generator that returns time differences
    ti = 0           # initial time
    tf = time.time() # final time
    while True:
        ti = tf
        tf = time.time()
        yield tf-ti # returns the time difference

TicToc = TicTocGenerator() # create an instance of the TicTocGen generator

# This will be the main function through which we define both tic() and toc()
def toc(tempBool=True):
    # Prints the time difference yielded by generator instance TicToc
    tempTimeInterval = next(TicToc)
    if tempBool:
        print( "Elapsed time: %f seconds.\n" %tempTimeInterval )

def tic():
    # Records a time in TicToc, marks the beginning of a time interval
    toc(False)
    
def pickler( obj, path):
    """
    Pickle a Python object
    """
    with open(path, "wb") as pfile:
        pkl.dump(obj, pfile)

def depickler( path):
    """
    Extracts a pickled Python object and returns it
    """
    with open(path, "rb") as pfile:
        data = pkl.load(pfile)
    return data


/home/rhagoletis/catkin/src/beginner/scripts/panda/world/venv/lib/python2.7/site-packages/matplotlib/font_manager.py:273: UserWarning: Matplotlib is building the font cache using fc-list. This may take a moment.
  warnings.warn('Matplotlib is building the font cache using fc-list. This may take a moment.')


In [9]:
'''
Load  bag filesto make into respective dataframes
'''
defaultPath="/home/rhagoletis/catkin/src/beginner/scripts/panda/world/bags/"
paths=easygui.fileopenbox(title="Bags to Dataframes"
                          ,default=defaultPath,
                          multiple=True,filetypes=["*traj.bag"])
print paths, "\n"
metadata=None

i=1
for path in paths:
    tic()
    print "starting analysis of file %s , %s / %s files" %(path.split('/')[-1],i,len(paths))
    df=rosbag_pandas.bag_to_dataframe(path,include=['/trajectory'])
    bag=rosbag.Bag(path)
    
    try:
        for topic,msg,t in bag.read_messages(topics='/metadata'):
            a=msg
        parameters=json.loads(a.data)
        metadata={"meta":parameters}

    except :
        print "no such file!"
    
    
#     metadataPath=path.split('traj.bag')[0]+'full' #get the filename of pickle file , it has no .bag
#     try:
#         with open(metadataPath, "rb") as pfile:
#             data = pkl.load(pfile)
#         parameters=data[0]
#         metadata={"meta":data}
#         print "metadata added"

#     except IOError:
#         "no  file %s"%(metadataPath)
        
    obj=dict(df=df,metadata=metadata)
    
    picklepath=path+"_df.pickle"
    pickler(obj,picklepath)
#     df.to_pickle(picklepath)
    
    i+=1
    toc()
print "\nanalysis of %s files complete" %len(paths)


['/home/rhagoletis/catkin/src/beginner/scripts/panda/world/bags/2016_08_24/traj/2016-08-24__18:30:51_fly10_quad_00_gain14_trial_1_traj.bag', '/home/rhagoletis/catkin/src/beginner/scripts/panda/world/bags/2016_08_24/traj/2016-08-24__18:34:20_fly10_quad_00_gain14_trial_1_traj.bag', '/home/rhagoletis/catkin/src/beginner/scripts/panda/world/bags/2016_08_24/traj/2016-08-24__20:44:08_fly11_quad_00_gain14_trial_1_traj.bag', '/home/rhagoletis/catkin/src/beginner/scripts/panda/world/bags/2016_08_24/traj/2016-08-24__20:45:50_fly11_quad_00_gain14_trial_1_traj.bag', '/home/rhagoletis/catkin/src/beginner/scripts/panda/world/bags/2016_08_24/traj/2016-08-24__20:54:28_fly11_quad_00_gain7_trial_1_traj.bag', '/home/rhagoletis/catkin/src/beginner/scripts/panda/world/bags/2016_08_24/traj/2016-08-24__21:32:11_fly11_quad_00_gain7_trial_1_traj.bag', '/home/rhagoletis/catkin/src/beginner/scripts/panda/world/bags/2016_08_24/traj/2016-08-24__21:41:07_fly11_quad_00_gain3.5_trial_1_traj.bag', '/home/rhagoletis/ca

In [16]:
data['metadata']['meta'].keys()

[u'world', u'servo', u'parameters', u'arduino']

In [10]:

def analyser(winTitle):
    
    '''
    takes window title input and returns average 
    compensation during stimulus period for each speed as a df
    '''
    #unknown rare bug, shabby fix
    df.trajectory__impose[0]=0
    
    impose=df.trajectory__impose.copy()
    impose[df.trajectory__impose==0]=1 #replace impose zero with one fordiv by zero
    compensation=df.trajectory__imposeResponse/impose
    compensationSmooth=df.trajectory__imposeResponseSmooth/impose

    cp = pd.DataFrame(index=compensation.index,columns=['a'])

    #flips are position where there is a rise or fall
    flips=np.sign(np.diff(df.trajectory__impose))

    #impose is impose df without first element
    impose=df.trajectory__impose.drop(df.trajectory__impose.index[0])

    #cw is clockWise, ccw is Counter clockwise
    #start and stop are positions where the impose starts or stops
    #start(stop) is zero everywhere except when there is the respective start(stop) event
    ccwStart=np.logical_and((flips==1) , (impose>0))
    ccwStop=np.logical_and((flips==-1) , (impose==0))
    cwStart=np.logical_and((flips==-1) , (impose<0))
    cwStop=np.logical_and((flips==1) , (impose==0))

#     plt.plot(np.array(impose),'r')
#     plt.plot(np.array(flips),'g')
#     plt.plot(np.array(ccwStart)*1,'b')
#     plt.plot(np.array(ccwStop)*1,'k')
#     plt.plot(np.array(cwStart)*1,'m')
#     plt.plot(np.array(cwStop)*1,'y')
#     print ccwStart.shape,ccwStop.shape
#     print cwStart.shape,cwStop.shape
#     plt.show()

    #(c)cwStart(stop)Index is just those positions where flips occured

    ccwStartIndex= ccwStart[ccwStart==1]
    cwStartIndex= cwStart[cwStart==1]
    ccwStopIndex= ccwStop[ccwStop==1]
    cwStopIndex= cwStop[cwStop==1]
#     print ccwStartIndex.shape,ccwStopIndex.shape
#     print cwStartIndex.shape,cwStopIndex.shape

#     print ccwStartIndex,ccwStopIndex
#     print cwStartIndex,cwStopIndex


    #compensationMean is a df who is zero when impose is false, 
    # and has mean value of compensation during the corresponding impose
    compensationMean = pd.DataFrame(index=compensation.index,columns=['mean']) #empty df with same index

    # print compensation
    def compMean(start,stop,compIn,compOut):
        consol=pd.DataFrame(columns=['fly','gain','impose','compensation'])


        print "calculating Mean"
        #if there are more starts than stop because of abrupt ending while recording
        #remove the last start event
        try: 
            assert len(start)==len(stop)
        except AssertionError:
            print 'assertion error'
            start=start[:-1] 

        for i in range(len(stop)):
#             print "impose is",df.trajectory__impose[start.index[i]]
#             print "gain is",df.trajectory__gain[start.index[i]]


#             print "i mean is",compIn.ix[start.index[i]:stop.index[i]].mean()
            currCompensationMean=compIn.ix[start.index[i]:stop.index[i]].mean()
            compOut.ix[start.index[i]:stop.index[i]]=currCompensationMean
            curr=pd.DataFrame([{'fly':parameters['fly'],
                                                 "gain":df.trajectory__gain[start.index[i]],
                                                 "impose":df.trajectory__impose[start.index[i]],
                                                 'compensation':currCompensationMean}])
            consol=consol.append(curr,ignore_index=True)        
        cols=['fly','gain','impose','compensation']
        consol=consol[cols]
#         print "total measn were",i+1
        return consol

    cw=compMean(cwStartIndex,cwStopIndex,compensation,cp)
    ccw=compMean(ccwStartIndex,ccwStopIndex,compensation,cp)
    
    
    
#     plt.plot(df.trajectory__imposeResponseSmooth,c=(0,0,1,0.2))
#     plt.plot(compensationSmooth,c=(1,0,0,0.6))
#     plt.plot(df.trajectory__impose)
#     plt.plot(cp,'g')
#     plt.axhline(y=1)
#     plt.title(winTitle)
#     plt.show()
    
    return ccw, cw


In [11]:
'''Load a dataframe from pickle'''
defaultPath="/home/rhagoletis/catkin/src/beginner/scripts/panda/world/bags/"
paths=easygui.fileopenbox(title="Bags to Dataframes"
                          ,default=defaultPath,
                          multiple=True,filetypes=["*df.pickle"])
fullConsol=pd.DataFrame()
# print paths, "\n"
for path in paths:
    
    tic()
    print "\n\ncurrentl;y analysisnh",path
    # picklepath=path+"_df.pickle"
    data=depickler(path)
    df=data["df"]
    parameters=data["metadata"]['meta']
    # df=pd.read_pickle(path)
    toc()
    Wtitle=path.split('/')[-1]
    print Wtitle
#     df.trajectory__imposeResponse.plot(title=path.split('/')[-1])
#     df.trajectory__impose.plot(title=path.split('/')[-1])


    
#     print "parameter keys are", parameters.keys()
#     print "\nparameter keys length are", len(parameters.keys())

#     plt.show()
    ccw,cw=analyser(Wtitle)
    fullConsol=fullConsol.append(ccw,ignore_index=True)
    fullConsol=fullConsol.append(cw,ignore_index=True)
    
print fullConsol



currentl;y analysisnh /home/rhagoletis/catkin/src/beginner/scripts/panda/world/bags/2016_08_24/traj/2016-08-24__18:34:20_fly10_quad_00_gain14_trial_1_traj.bag_df.pickle
Elapsed time: 1.134909 seconds.

2016-08-24__18:34:20_fly10_quad_00_gain14_trial_1_traj.bag_df.pickle
calculating Mean


/usr/local/lib/python2.7/dist-packages/ipykernel/__main__.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


KeyError: 'fly'

In [ ]:
ccw,cw=analyser(Wtitle)
fullConsol=fullConsol.append(ccw,ignore_index=True)
fullConsol=fullConsol.append(cw,ignore_index=True)

In [31]:
from bokeh.plotting import figure, output_file, show
from bokeh.models.widgets import Panel, Tabs
output_file("line.html")

x=df.trajectory__impose.index
y1=df.trajectory__impose
y2=df.trajectory__imposeResponse
y3=df.trajectory__imposeResponseSmooth
y4=compensationSmooth
y5=cp.fillna(0).abs()
# y5=cp

p1 = figure(plot_width=800, plot_height=800, y_range=(-3,3),x_axis_type="datetime")
p2 = figure(plot_width=800, plot_height=800, y_range=(-3,3),x_axis_type="datetime")
p3 = figure(plot_width=800, plot_height=800, y_range=(-3,3),x_axis_type="datetime")
p4 = figure(plot_width=800, plot_height=800, y_range=(-3,3),x_axis_type="datetime")
p5 = figure(plot_width=800, plot_height=800, y_range=(-3,3),x_axis_type="datetime")

p1.line(x,y1, line_width=2, line_color="navy")

p2.line(x,y2, line_width=0.75,line_color="orange",line_alpha=0.2)

p3.line(x,y1, line_width=2, line_color="navy")
p3.line(x,y2, line_width=0.75,line_color="orange",line_alpha=0.2)
p3.line(x,y3, line_width=1,line_color="olive",line_alpha=1)

p4.line(x,y1, line_width=2, line_color="navy")
p4.line(x,y3, line_width=0.75,line_color="orange",line_alpha=0.5)
p4.line(x,y4, line_width=1,line_color="olive",line_alpha=0.5)

p5.line(x,y5, line_width=2,line_color="darkgrey",line_alpha=1)
p5.line(x,y1, line_width=2, line_color="navy")
p5.line(x,y3, line_width=0.75,line_color="orange",line_alpha=0.5)
p5.line(x,y4, line_width=1,line_color="olive",line_alpha=0.5)


tab1 = Panel(child=p1, title="impose")
tab2 = Panel(child=p2, title="imposeResponse")
tab3 = Panel(child=p3, title="imposeResponseSmooth")
tab4 = Panel(child=p4, title="compensation")
tab5 = Panel(child=p5, title="compensationMean")




tabs = Tabs(tabs=[tab1,tab2,tab3,tab4 ,tab5])

show(tabs)


In [5]:


'''
takes window title input and returns average 
compensation during stimulus period for each speed as a df
'''
#unknown rare bug, shabby fix
df.trajectory__impose[0]=0

impose=df.trajectory__impose.copy()
impose[df.trajectory__impose==0]=1 #replace impose zero with one fordiv by zero
compensation=df.trajectory__imposeResponse/impose
compensationSmooth=df.trajectory__imposeResponseSmooth/impose

cp = pd.DataFrame(index=compensation.index,columns=['a'])

#flips are position where there is a rise or fall
flips=np.sign(np.diff(df.trajectory__impose))

#impose is impose df without first element
impose=df.trajectory__impose.drop(df.trajectory__impose.index[0])

#cw is clockWise, ccw is Counter clockwise
#start and stop are positions where the impose starts or stops
#start(stop) is zero everywhere except when there is the respective start(stop) event
ccwStart=np.logical_and((flips==1) , (impose>0))
ccwStop=np.logical_and((flips==-1) , (impose==0))
cwStart=np.logical_and((flips==-1) , (impose<0))
cwStop=np.logical_and((flips==1) , (impose==0))

#     plt.plot(np.array(impose),'r')
#     plt.plot(np.array(flips),'g')
#     plt.plot(np.array(ccwStart)*1,'b')
#     plt.plot(np.array(ccwStop)*1,'k')
#     plt.plot(np.array(cwStart)*1,'m')
#     plt.plot(np.array(cwStop)*1,'y')
#     print ccwStart.shape,ccwStop.shape
#     print cwStart.shape,cwStop.shape
#     plt.show()

#(c)cwStart(stop)Index is just those positions where flips occured

ccwStartIndex= ccwStart[ccwStart==1]
cwStartIndex= cwStart[cwStart==1]
ccwStopIndex= ccwStop[ccwStop==1]
cwStopIndex= cwStop[cwStop==1]
#     print ccwStartIndex.shape,ccwStopIndex.shape
#     print cwStartIndex.shape,cwStopIndex.shape

#     print ccwStartIndex,ccwStopIndex
#     print cwStartIndex,cwStopIndex


#compensationMean is a df who is zero when impose is false, 
# and has mean value of compensation during the corresponding impose
compensationMean = pd.DataFrame(index=compensation.index,columns=['mean']) #empty df with same index

# print compensation
def compMean(start,stop,compIn,compOut):
    consol=pd.DataFrame(columns=['fly','gain','impose','compensation'])


    print "calculating Mean"
    #if there are more starts than stop because of abrupt ending while recording
    #remove the last start event
    try: 
        assert len(start)==len(stop)
    except AssertionError:
        print 'assertion error'
        start=start[:-1] 

    for i in range(len(stop)):
#             print "impose is",df.trajectory__impose[start.index[i]]
#             print "gain is",df.trajectory__gain[start.index[i]]


#             print "i mean is",compIn.ix[start.index[i]:stop.index[i]].mean()
        currCompensationMean=compIn.ix[start.index[i]:stop.index[i]].mean()
        compOut.ix[start.index[i]:stop.index[i]]=currCompensationMean
        curr=pd.DataFrame([{'fly':parameters['fly'],
                                             "gain":df.trajectory__gain[start.index[i]],
                                             "impose":df.trajectory__impose[start.index[i]],
                                             'compensation':currCompensationMean}])
        consol=consol.append(curr,ignore_index=True)        
    cols=['fly','gain','impose','compensation']
    consol=consol[cols]
#         print "total measn were",i+1
    return consol

cw=compMean(cwStartIndex,cwStopIndex,compensation,cp)
ccw=compMean(ccwStartIndex,ccwStopIndex,compensation,cp)



#     plt.plot(df.trajectory__imposeResponseSmooth)
#     plt.plot(compensation,c=(1,0,0,0.2))
#     plt.plot(df.trajectory__impose)
# #     plt.plot(cp,'g')
#     plt.axhline(y=1)
#     plt.title(winTitle)
#     plt.show()



calculating Mean
calculating Mean


/usr/local/lib/python2.7/dist-packages/ipykernel/__main__.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


In [9]:
import seaborn as sns
sns.set_style("whitegrid")

In [12]:
ax = sns.stripplot(hue=fullConsol['impose'].round(1).abs(),   jitter=True,
                   y=fullConsol['compensation'],x=fullConsol['gain'],
                   split=True,palette="BuGn",linewidth=1)
plt.show()

In [29]:
ax = sns.stripplot(x=fullConsol['impose'].round(1).abs(),   jitter=True,
                   y=fullConsol['compensation'],hue=fullConsol['gain'],
                   split=True,palette="BuGn",linewidth=1)
plt.show()

In [13]:
plt.plot(fullConsol.impose,fullConsol.compensation)
plt.show()

In [15]:
pickler(fullConsol,'consolidatedDF')

In [16]:
a=depickler('consolidatedDF')

In [28]:
a['impose']=a['impose'].abs()
b=a.groupby(['fly','gain','impose'],as_index=False).mean()

ax = sns.stripplot(hue=b['impose'].round(1).abs(),   jitter=True,
                   y=b['compensation'],x=b['gain'],split=True,palette="viridis_r",size=8)
plt.show()

In [ ]:
impose=df.trajectory__impose.copy()
impose[df.trajectory__impose==0]=1 #replace impose zero with one fordiv by zero
compensation=df.trajectory__imposeResponseSmooth/impose
# plt.plot(df.trajectory__imposeResponseSmooth)
plt.plot(compensation,c=(1,0,0,0.2))
plt.plot(df.trajectory__impose)
plt.plot(cp,'g')
plt.axhline(y=1)
plt.show()

In [ ]:
parameters

In [ ]:
#flips are position where there is a rise or fall
flips=np.sign(np.diff(df.trajectory__impose))

#impose is impose df without first element
impose=df.trajectory__impose.drop(df.trajectory__impose.index[0])

#cw is clockWise, ccw is Counter clockwise
#start and stop are positions where the impose starts or stops
#start(stop) is zero everywhere except when there is the respective start(stop) event
ccwStart=np.logical_and((flips==1) , (impose>0))
ccwStop=np.logical_and((flips==-1) , (impose==0))
cwStart=np.logical_and((flips==-1) , (impose<0))
cwStop=np.logical_and((flips==1) , (impose==0))

# plt.plot(np.array(impose),'r')
# plt.plot(np.array(flips),'g')
# plt.plot(np.array(ccwStart)*1,'b')
# plt.plot(np.array(ccwStop)*1,'k')
# plt.plot(np.array(cwStart)*1,'m')
# plt.plot(np.array(cwStop)*1,'y')
# print ccwStart.shape,ccwStop.shape
# print cwStart.shape,cwStop.shape
plt.show()

#(c)cwStart(stop)Index is just those positions where flips occured

ccwStartIndex= ccwStart[ccwStart==1]
cwStartIndex= cwStart[cwStart==1]
ccwStopIndex= ccwStop[ccwStop==1]
cwStopIndex= cwStop[cwStop==1]
print ccwStartIndex.shape
print ccwStopIndex.shape

print cwStartIndex.shape
print cwStopIndex.shape


cp = pd.DataFrame(index=compensation.index,columns=['a'])

#compensationMean is a df who is zero when impose is false, 
# and has mean value of compensation during the corresponding impose
compensationMean = pd.DataFrame(index=compensation.index,columns=['mean']) #empty df with same index

# print compensation
def compMean(start,stop,compIn,compOut):
    print "calculating Mean"
    #if there are more starts than stop because of abrupt ending while recording
    #remove the last start event
    try: 
        assert len(start)==len(stop)
    except AssertionError:
        print 'assertion error'
        start=start[:-1] 

    for i in range(len(stop)):

        print "i mean is",compIn.ix[start.index[i]:
                                          stop.index[i]].mean()
        compOut.ix[start.index[i]:stop.index[i]]=compIn.ix[start.index[i]:stop.index[i]].mean()

    print "total measn were",i+1
compMean(cwStartIndex,cwStopIndex,compensation,cp)
compMean(ccwStartIndex,ccwStopIndex,compensation,cp)

In [ ]:
df.trajectory__imposeResponse.plot()
df.trajectory__impose.plot()

plt.show()

In [ ]:
plt.plot(pd.rolling_mean((df.trajectory__imposeResponse),window=10))
plt.plot(pd.rolling_mean((df.trajectory__imposeResponse),window=100),'r')
plt.show()
         

In [ ]:
# ccwStart=pd.DataFrame(0, index=np.arange(len(df)), columns=["feature_list"])
flips=np.sign(df.trajectory__impose.diff)
ccwStart[flips>0]=1
plt.plot(flips)
plt.show()

In [ ]:
flips=np.sign(np.diff(df.trajectory__impose))
impose=df.trajectory__impose.drop(df.trajectory__impose.index[1])
# a=np.roll(a,-1)
ccwStart=np.logical_and((flips==1) , (impose>0))
ccwStop=np.logical_and((flips==-1) , (impose==0))
cwStart=np.logical_and((flips==-1) , (impose<0))
cwStop=np.logical_and((flips==1) , (impose==0))

plt.plot(np.array(impose),'r')
plt.plot(np.array(flips),'g')
plt.plot(np.array(ccwStart)*1,'b')
plt.plot(np.array(ccwStop)*1,'k')
plt.plot(np.array(cwStart)*1,'m')
plt.plot(np.array(cwStop)*1,'y')
print ccwStart.shape,ccwStop.shape
print cwStart.shape,cwStop.shape

ccwStart= ccwStart[ccwStart==1]
cwStart= cwStart[cwStart==1]
ccwStop= ccwStop[ccwStop==1]
cwStop= cwStop[cwStop==1]
print ccwStart,ccwStop

plt.show()

In [ ]:
cp = pd.DataFrame(index=compensation.index,columns=['a'])
# print compensation
for i in range(len(ccwStart)):
    try: 
        assert len(ccwStart)==len(ccwStop)
    except AssertionError:
        ccwStop=ccwStop[:-1]
    
    print "i mean is",compensation.ix[cwStart.index[i]:
                                      cwStop.index[i]].mean()
    cp.ix[cwStart.index[i]:cwStop.index[i]]=compensation.ix[cwStart.index[i]:cwStop.index[i]].mean()
    

In [ ]:
a={'a':1,'b':2,'c':3,'d':5}
b={'a':2,'b':2,'c':3,'d':5}

# d.append(df, ignore_index=True)
df=pd.DataFrame([a])
df=df.append(pd.DataFrame([b]))#,ignore_index=True)
print df
# print d

In [ ]:
a

In [ ]:
print (df.trajectory__impose.shape)
a.shape

In [ ]:
(.3195+.34179)/2

In [ ]:
plt.plot(flips)
plt.plot(np.array(b),'r')

plt.show()

In [ ]:
df.trajectory__wbad.plot.hist(bins=60)

In [ ]:
''' 
Load multiple dataframe pickle file into memory and append it
'''
paths=easygui.fileopenbox(multiple=True,filetypes=['*.pickle'])
i=0
a=range(len(paths))
for path in paths:
    a[i]=pd.read_pickle(path)

    i+=1
    
df=pd.concat(a)

In [ ]:
#load params pickle
path=easygui.fileopenbox()
import cPickle as pl
import json
a=pl.load(open( path, "rb" ))
params=a[1]

In [37]:
parameters


{u'DCoffset': 0.31,
 u'DCoffsetIncrement': 0.002,
 u'age': 50,
 u'bagTopics': u'/usb_cam/image_raw /kinefly/image_output /kinefly/flystate /trajectory',
 u'bboxDist': 7.5,
 u'camFOV': [178, 140],
 u'camHpr': [0, -2, 0],
 u'captureScale': 1,
 u'captureStart': 0,
 u'disabledFly': False,
 u'emergence': 20160507,
 u'fly': u'fly8',
 u'fps': 165,
 u'frameNum': 0,
 u'frameRecord': False,
 u'gain': 7.0,
 u'gainIncrement': 0.02,
 u'generateWorld': False,
 u'greenTexPath': u'models/green.tga',
 u'hcp': False,
 u'heightObjects': 10,
 u'initPosList': [[193.0, 161.0, 3],
  [64, 161.0, 3],
  [64, 32, 3],
  [193.0, 32, 3]],
 u'killWorldGen': True,
 u'lattice': 25,
 u'loadHUD': False,
 u'loadOdour': True,
 u'loadTrajectory': True,
 u'loadWind': True,
 u'loadWorld': True,
 u'loadingString': u'00',
 u'lockFps': True,
 u'lrGain': 1.0,
 u'maxBoutDur': 9900,
 u'maxDistance': 65,
 u'maxSpeed': 3.5,
 u'modelHeightMap': u'models/height2570.png',
 u'modelSizeSuffix': u'257',
 u'modelTextureMap': u'models/textu

In [63]:
df.trajectory__trial.max()

22.0

In [ ]:
''' 
Load multiple bag files to be converted to dataframe
'''

paths=easygui.fileopenbox(multiple=True,filetypes=['*.bag'])
i=0
for path in paths:

    df=rosbag_pandas.bag_to_dataframe(path,include=['/trajectory'])
    df.columns
    bag=rosbag.Bag(path)
    for topic,msg,t in bag.read_messages(topics='/metadata'):
        a=msg
    parameters=json.loads(a.data)
    picklepath=path+"_df.pickle"
    df.to_pickle(picklepath)
    i+=1
    
print "done"

In [64]:
'''
plot a single df
'''
params=parameters
from bokeh.plotting import figure, output_file, show
parameters['odourField']=(np.array(parameters['odourField']['__ndarray__']))
# prepare some data
N = len(df.trajectory__position_x)
x = df.trajectory__position_x
y = df.trajectory__position_y
h=np.deg2rad(df.trajectory__orientation_x)

dec=1
x=x[::dec]
y=y[::dec]
h=h[::dec]
colors = [
    "#%02x%02x%02x" % (int(r), int(g), 150) for r, g in zip(50+2*x, 30+2*y)
]

# output to static HTML file (with CDN resources)
output_file(path+".html", title="Trajectory Quad", mode="cdn")

TOOLS="resize,crosshair,pan,wheel_zoom,box_zoom,reset,box_select,lasso_select,undo,redo,save"

# create a new plot with the tools above, and explicit ranges
p = figure(tools=TOOLS, x_range=(0,256), y_range=(0,256),webgl=True,plot_width=1000, plot_height=1000)
p.image(image=[np.flipud(np.rot90(np.invert((params["odourField"])>0)*1))], 
        x=0, y=0, dw=255, dh=255, palette="Greys9")

# add a circle renderer with vectorized colors and sizes
# p.circle(x,y,size=4  ,fill_alpha=0.5, line_color=None)
p.triangle(x,y,size=10 ,angle=h ,fill_alpha=0.8, line_color=None)
# p.wedge(x, y, radius=0.2, start_angle=0.4, end_angle=4.8,
#         color="firebrick", alpha=0.6, direction="clock")
# show the results
show(p)

In [57]:
'''plotdoor field'''
p = figure(x_range=(0, 255), y_range=(0,255))

p.image(image=[np.flipud(np.rot90(params["odourField"]))], x=0, y=0, dw=255, dh=255, palette="Greys3")


# must give a vector of image data for image parameter

output_file("image.html", title="image.py example")

show(p)  # open a browser

In [ ]:
#load df pickle
path=easygui.fileopenbox()
df=pd.read_pickle(path)
path=path.rstrip("_df.pickle")

In [ ]:
files=easygui.fileopenbox("select the files to be dataframed and plotted",multiple=True)

In [58]:
'''
plot a single df
'''

from bokeh.plotting import figure, output_file, show, gridplot

# prepare some data
N = len(df.trajectory__position_x)
x = df.trajectory__position_x
y = df.trajectory__position_y
h=np.deg2rad(df.trajectory__orientation_x)

dec=6
x=x[::dec]
y=y[::dec]
h=h[::dec]
colors = [
    "#%02x%02x%02x" % (int(r), int(g), 150) for r, g in zip(50+2*x, 30+2*y)
]

# output to static HTML file (with CDN resources)
output_file(path+".html", title="Trajectory Quad", mode="cdn")

TOOLS="resize,crosshair,pan,wheel_zoom,box_zoom,reset,box_select,lasso_select,undo,redo,save"

# create a new plot with the tools above, and explicit ranges
w=500
h=500 
s=3
bl = figure(tools=TOOLS, x_range=(64-32,64+32), y_range=(32-32,32+32),webgl=True,plot_width=w, plot_height=h)
tl = figure(tools=TOOLS, x_range=(64-32,64+32), y_range=(161-32,161+32),webgl=True,plot_width=w, plot_height=h)
br = figure(tools=TOOLS, x_range=(193-32,193+32), y_range=(32-32,32+32),webgl=True,plot_width=w, plot_height=h)
tr = figure(tools=TOOLS, x_range=(193-32,193+32), y_range=(161-32,161+32),webgl=True,plot_width=w, plot_height=h)

bl.triangle(x,y,size=s ,angle=h ,fill_alpha=1, line_color=None)
tl.triangle(x,y,size=s ,angle=h ,fill_alpha=1, line_color=None)
br.triangle(x,y,size=s ,angle=h ,fill_alpha=1, line_color=None)
tr.triangle(x,y,size=s ,angle=h ,fill_alpha=1, line_color=None)

bl.image(image=[np.flipud(np.rot90(np.invert((params["odourField"])>0)*1))], 
        x=0, y=0, dw=255, dh=255, palette="Greys9")


tl.image(image=[np.flipud(np.rot90(np.invert((params["odourField"])>0)*1))], 
        x=0, y=0, dw=255, dh=255, palette="Greys9")

br.image(image=[np.flipud(np.rot90(np.invert((params["odourField"])>0)*1))], 
        x=0, y=0, dw=255, dh=255, palette="Greys9")

tr.image(image=[np.flipud(np.rot90(np.invert((params["odourField"])>0)*1))], 
        x=0, y=0, dw=255, dh=255, palette="Greys9")

p = gridplot([[tl, tr], [bl, br]])

# add a circle renderer with vectorized colors and sizes
# p.circle(x,y,size=4  ,fill_alpha=0.5, line_color=None)
# p.triangle(x,y,size=4 ,angle=h ,fill_alpha=1, line_color=None)
# p.wedge(x, y, radius=0.2, start_angle=0.4, end_angle=4.8,
#         color="firebrick", alpha=0.6, direction="clock")
# show the results
show(p)

In [41]:
params["odourField"]

{u'__ndarray__': [[0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,


In [ ]:
a=range(0,15)
a=a[::5]
a

In [59]:
import numpy as np

from bokeh.plotting import figure, show, output_file

N = 1000
x = np.linspace(0, 10, N)
y = np.linspace(0, 10, N)
xx, yy = np.meshgrid(x, y)
d = np.sin(xx)*np.cos(yy)

p = figure(x_range=(0, 10), y_range=(0, 10))

# must give a vector of image data for image parameter
p.image(image=[d], x=0, y=0, dw=10, dh=10, color_mapper=1)

output_file("image.html", title="image.py example")

show(p)  # open a browser

ValueError: expected an instance of type ColorMapper, got 1 of type int

In [60]:
from hcpWorldGen import WorldGen
df.plot.scatter('trajectory__position_x',y='trajectory__position_y',s=0.01)
# plt.show()

ImportError: No module named hcpWorldGen

In [65]:
import numpy as np
import matplotlib.pyplot as plt
import pickle as pl

# Plot simple sinus function
fig_handle = plt.figure()

plt.scatter(df.trajectory__position_x,df.trajectory__position_y,s=0.01)

# plt.scatter(initPlot.odd[:,0],initPlot.odd[:,1],color=initPlot.oddPlotColor,marker=initPlot.oddPlotMarker)
# plt.scatter(initPlot.even[:,0],initPlot.even[:,1],color=initPlot.evenPlotColor,marker=initPlot.evenPlotMarker),marker='|',color='g')
# plt.axis([0,255,0,255])

plt.show()


# Save figure handle to disk
# pl.dump(fig_handle,file('sinus.pickle','w'))



In [ ]:
print type(fig_handle)

In [ ]:
p.image(image=[d], x=0, y=0, dw=10, dh=10, palette="Spectral11")

In [ ]:
'''plot hex bin'''

df.plot.hexbin(x='trajectory__position_x',y='trajectory__position_y',gridsize=10,cmap=plt.cm.viridis,)
plt.show()


In [ ]:
WorldGen.initPositions

In [ ]:
df.plot.hexbin(x='trajectory__position_x',y='trajectory__position_y',gridsize=100)

In [ ]:
plt.show()

In [ ]:
df.columns

In [ ]:
plt.imshow(np.flipud(np.rot90(params["odourField"])))
plt.show()

In [ ]:
params["odourField"].shape

In [ ]:
params

In [ ]:
a[1]

In [ ]:
2+3

In [ ]:
print paths

In [ ]:
# modules
#------------------------------------------------------------------------------
import numpy as np
import matplotlib.pyplot as py
from matplotlib import animation

py.close('all') # close all previous plots

# create a random line to plot
#------------------------------------------------------------------------------

x = df.trajectory__position_x
y = df.trajectory__position_y
t = np.linspace(0,1,x.shape[0]) # your "time" variable
# py.figure(1)
# py.scatter(0, 0, s=1)
# py.axis([0, 255, 0, 255])
# py.show()

# animation of a scatter plot using x, y from above
#------------------------------------------------------------------------------

fig = py.figure(1)
ax = py.axes(xlim=(0, 255), ylim=(0,255))
scat = ax.scatter([], [], s=20,marker=(3,0,0))

def init():
    scat.set_offsets([])
    return scat,

def animate(i):
    data = np.hstack((x[:i,np.newaxis], y[:i, np.newaxis]))
    scat.set_offsets(data)
    scat.se
#     scat.set_marker('o')
    return scat,

anim = animation.FuncAnimation(fig, animate, init_func=init, frames=len(x)+1, 
                               interval=1000/165., blit=True, repeat=False)
plt.show()

In [ ]:
len(df.trajectory__position_x)

In [ ]:
i=360


In [ ]:
import matplotlib


In [ ]:
print matplotlib.__version__